## Import thư viện

In [2]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from bs4 import BeautifulSoup
import csv
import time
import random

## Lấy dữ liệu từ Chrome

In [10]:
countries = ['vietnam', 'thailand', 'singapore', 'malaysia', 'indonesia', 'cambodia', 'philippines']

countries_links = ['https://www.traveloka.com/vi-vn/hotel/' + country for country in countries]
regions_links = []
hotels_links = []

### Lấy link khách sạn các quốc gia

In [ ]:
driver = webdriver.Chrome()

for country in countries:
    country_link = f'https://www.traveloka.com/vi-vn/hotel/{country}'
    driver.get(country_link)
    time.sleep(5)

    soup = BeautifulSoup(driver.page_source, 'html.parser')  # Lấy source HTML

    for link in soup.find_all('a', class_='css-4rbku5', href=True):
        href = link['href']
        if href.startswith(f'/vi-vn/hotel/{country}'):
            full_url = 'https://www.traveloka.com' + href

            suffix = href[len(f'/vi-vn/hotel/{country}/'):]  # phần sau /vi-vn/hotel/{country}/
            first_segment = suffix.split('/')[0]

            if first_segment in ['region', 'area', 'city', 'landmark']:
                if full_url not in regions_links:
                    regions_links.append(full_url)
            else:
                if full_url not in hotels_links:
                    hotels_links.append(full_url)      

print(f'Tìm thấy {len(regions_links)} vùng khách sạn và {len(hotels_links)} khách sạn.')


In [ ]:
# regions_links.clear()
# hotels_links.clear()

### Lấy link khách sạn các phân vùng của mỗi quốc gia

#### b. Crawl phân vùng những lần sau (chạy trước khi chạy cell dưới)

In [11]:
# append data trong file regions_links.csv vào list regions_links
with open('regions_links.csv', 'r', encoding='utf-8') as f:
    reader = csv.reader(f)
    next(reader)  # Bỏ dòng tiêu đề
    for row in reader:
        if row:
            regions_links.append(row[0])

# URL bắt đầu và kết thúc
start_url = "https://www.traveloka.com/vi-vn/hotel/malaysia/area/dengkil-108048"
end_url   = "https://www.traveloka.com/vi-vn/hotel/philippines/city/lubao-10008325"

# Xác định vị trí index bắt đầu và kết thúc
try:
    start_index = regions_links.index(start_url)
    end_index = regions_links.index(end_url)
except ValueError as e:
    print("Không tìm thấy URL trong danh sách:", e)
    exit()

# Giới hạn danh sách cần crawl
regions_links_to_crawl = regions_links[start_index:end_index + 1]

#### a. Crawl phân vùng (đổi thành in regions_links_to_crawl ở những lần crawl sau)

In [12]:
driver = webdriver.Chrome()

for region_link in regions_links_to_crawl: # lần đầu thì in regions_links
    driver.get(region_link)
    time.sleep(random.uniform(3,7))

    soup = BeautifulSoup(driver.page_source, 'html.parser')  # Lấy source HTML

    for link in soup.find_all('a', class_='css-4rbku5', href=True):
        href = link['href']
        if href.startswith(f'/vi-vn/hotel/'):
            full_url = 'https://www.traveloka.com' + href

            suffix = href[len(f'/vi-vn/hotel/'):]  # phần sau /vi-vn/hotel/{country}/
            segments = suffix.split('/')

            if len(segments) >=2:
                if segments[1] in ['region', 'area', 'city', 'landmark']:
                    if full_url not in regions_links:
                        regions_links.append(full_url)
                else:
                    if full_url not in hotels_links:
                        hotels_links.append(full_url)

In [13]:
print('\n'.join(regions_links))

https://www.traveloka.com/vi-vn/hotel/vietnam/city/district-1-10010551
https://www.traveloka.com/vi-vn/hotel/vietnam/region/hanoi-10009843
https://www.traveloka.com/vi-vn/hotel/vietnam/city/phu-quoc-10011570
https://www.traveloka.com/vi-vn/hotel/vietnam/region/da-nang-10010083
https://www.traveloka.com/vi-vn/hotel/vietnam/city/nha-trang-10010498
https://www.traveloka.com/vi-vn/hotel/vietnam/city/district-10-10010559
https://www.traveloka.com/vi-vn/hotel/vietnam/city/district-3-10010552
https://www.traveloka.com/vi-vn/hotel/vietnam/city/da-lat-10010169
https://www.traveloka.com/vi-vn/hotel/vietnam/region/ho-chi-minh-city-10009794
https://www.traveloka.com/vi-vn/hotel/vietnam/city/tan-binh-district-10010618
https://www.traveloka.com/vi-vn/hotel/vietnam/region/quang-ninh-province-10009904
https://www.traveloka.com/vi-vn/hotel/vietnam/region/khanh-hoa-province-10009841
https://www.traveloka.com/vi-vn/hotel/vietnam/region/binh-duong-province-10010019
https://www.traveloka.com/vi-vn/hotel/vi

In [14]:
# Ghi region links ra file CSV (sau mỗi lần crawl phân vùng khách sạn thì chạy lại)
with open('regions_links.csv', 'w', newline='', encoding='utf-8') as f:
    writer = csv.writer(f)
    writer.writerow(['Region URL'])  # Tiêu đề cột
    for link in regions_links:
        writer.writerow([link])  # Mỗi link là một dòng

In [ ]:
# Ghi hotel links ra file CSV (chỉ chạy khi crawl phân vùng lần đầu)
with open('hotels_links.csv', 'w', newline='', encoding='utf-8') as f:
    writer = csv.writer(f)
    writer.writerow(['Hotel URL'])  # Tiêu đề cột
    for link in hotels_links:
        writer.writerow([link])  # Mỗi link là một dòng

In [16]:
# Ghi tiếp các URL mới vào hotels_links.csv (chạy khi crawl phân vùng những lần sau)
with open('hotels_links.csv', 'a', newline='', encoding='utf-8') as f:
    writer = csv.writer(f)
    for url in hotels_links:
        writer.writerow([url])

In [15]:
print('\n'.join(hotels_links))

https://www.traveloka.com/vi-vn/hotel/malaysia/langit-langi-hotel-2000000233039?contexts=%7B%22accessCode%22%3A%222023VNSEO2023%22%7D
https://www.traveloka.com/vi-vn/hotel/malaysia/coop-hotel-putrajaya-cyberjaya-4000000474782?contexts=%7B%22accessCode%22%3A%222023VNSEO2023%22%7D
https://www.traveloka.com/vi-vn/hotel/malaysia/sky-view-hotel-dengkil-putrajaya-9000000961968?contexts=%7B%22accessCode%22%3A%222023VNSEO2023%22%7D
https://www.traveloka.com/vi-vn/hotel/malaysia/1fish-guardway-1000001533856?contexts=%7B%22accessCode%22%3A%222023VNSEO2023%22%7D
https://www.traveloka.com/vi-vn/hotel/malaysia/d-boutique-hotel-dengkil-3000010019425?contexts=%7B%22accessCode%22%3A%222023VNSEO2023%22%7D
https://www.traveloka.com/vi-vn/hotel/malaysia/q-one-hotel-dengkil-3000010021504?contexts=%7B%22accessCode%22%3A%222023VNSEO2023%22%7D
https://www.traveloka.com/vi-vn/hotel/malaysia/oyo-90294-foong-inn-dengkil-9000000973406?contexts=%7B%22accessCode%22%3A%222023VNSEO2023%22%7D
https://www.traveloka.co

In [ ]:
if (len(hotels_links) > len(set(hotels_links))): # kiểm tra trùng data
    print("trung data")

## Lặp qua các url khách sạn

In [ ]:
# Tạo danh sách chứa dữ liệu
data = []

In [ ]:
for idx, link in enumerate(hotels_links[:10]):  # Crawl thử 10 khách sạn đầu
    print(f'📥 Đang crawl: {link}')
    driver.get(link)
    time.sleep(5)

    hotel_soup = BeautifulSoup(driver.page_source, 'html.parser')

    # --- Ví dụ lấy dữ liệu ---
    name = hotel_soup.find('h1').text.strip() if hotel_soup.find('h1') else ''
    address = hotel_soup.find('span', class_='address-text')  # ví dụ
    address = address.text.strip() if address else ''

    price = hotel_soup.find('span', class_='price-text')  # ví dụ
    price = price.text.strip() if price else ''

    # Lấy tiện ích (danh sách các <li>, <span>, <div> chứa icon + text)
    amenities = hotel_soup.find_all('div', class_='facilities-name')  # ví dụ
    amenity_list = ', '.join([a.text.strip() for a in amenities]) if amenities else ''

    data.append([name, address, price, amenity_list])

## Ghi vào file csv

In [ ]:
with open('hotels_detail.csv', 'w', newline='', encoding='utf-8-sig') as f:
    writer = csv.writer(f)
    writer.writerow(['Tên khách sạn', 'Địa chỉ', 'Giá', 'Tiện ích'])
    writer.writerows(data)

driver.quit()
print('✅ Crawl hoàn tất. Đã lưu file hotels_detail.csv')


✅ Crawl xong, đã lưu file hotels.csv!
